In [3]:
from tqdm import tqdm
from os import listdir
import json
import pickle

import torch
import torchvision
from torchvision.io import read_video
from torchvision.ops import box_convert

from torchvision.models.detection import maskrcnn_resnet50_fpn, MaskRCNN_ResNet50_FPN_Weights
from torchvision.utils import draw_bounding_boxes
import torchvision.transforms.functional as F

import cv2 as cv
import numpy as np
from scipy.spatial import distance

import matplotlib.pyplot as plt

## Required data 

In [4]:
scene_graph_path = f'../DVUChallenge/dev_dataset/scenes_knowledge_graphs/'

shots_data_path = f'../DVUChallenge/dev_dataset/movie.shots/'

dec_rate = 50

filmnames = [file for file in listdir(f'../DVUChallenge/dev_dataset/movie_knowledge_graph/') if '.' not in file]

### Scene graphs

In [ ]:
from general_utils import get_scene_graphs

scene_graphs = get_scene_graphs(filmnames, scene_graph_path)

In [5]:
with open('../DVUChallenge/dev_dataset/vocab.dvu.json', 'r') as f:
    scene_vocab = json.load(f)

### Video

In [6]:
from general_utils import get_videos

videos = get_videos(filmnames, shots_data_path, dec_rate)

  0%|          | 0/67 [00:00<?, ?it/s]/home/jovyan/.imgenv-bold-wing-0/lib/python3.7/site-packages/torchvision/io/video.py:162: UserWarning: The pts_unit 'pts' gives wrong results. Please use pts_unit 'sec'.
  warnings.warn("The pts_unit 'pts' gives wrong results. Please use pts_unit 'sec'.")

 93%|█████████▎| 70/75 [00:35<00:03,  1.36it/s]


100%|██████████| 14/14 [05:09<00:00, 22.11s/it]


### GRAPHEN tracking data

In [7]:
graphen_raw = {filmname:[] for filmname in filmnames}

for filmname in filmnames:
    with open(f'graphen_tracking/{filmname}_graphen_tracking.pickle', 'rb') as handle:
        graphen_raw[filmname] = pickle.load(handle)

### EVG tracking data

In [8]:
with open(f'../face_tracking_dr_{dec_rate}.json', 'r') as f:
    face_rec_res_d = json.load(f)

In [21]:
face_rec_res_d['Bagman'][0][10]

[['jack'],
 [[810.2653257772326,
   161.90951722860336,
   1073.2284514158964,
   506.05057549476624,
   0.9999990463256836]]]

In [19]:
for filmname in tqdm(filmnames):
    for scene_idx in range(len(face_rec_res_d[filmname])):
        for frame_idx in range(len(face_rec_res_d[filmname][scene_idx])):
            if len(face_rec_res_d[filmname][scene_idx][frame_idx]) == 0:
                face_rec_res_d[filmname][scene_idx][frame_idx] = [[], []]

100%|██████████| 14/14 [00:00<00:00, 1065.61it/s]


In [9]:
tracking_data_c = {filmname:[] for filmname in filmnames}

for filmname in tqdm(filmnames):
    scene_shots = [file for file in listdir(shots_data_path) if filmname in file]
    for i in range(len(scene_shots)):
        scene_number = i+1
        with open(f'lighttrack/data/demo/jsons/{filmname}_{scene_number}_dr_{dec_rate}_compressed.json', 'r') as f:
            tracking_data_c[filmname].append(json.load(f)) 

100%|██████████| 14/14 [00:07<00:00,  1.88it/s]


In [10]:
for filmname in tqdm(filmnames):
    for i in tqdm(range(len(tracking_data_c[filmname]))): #scene
        for j in range(len(tracking_data_c[filmname][i])): #frame
            for k in range(len(tracking_data_c[filmname][i][j]['candidates'])):
                pose_box = np.array(tracking_data_c[filmname][i][j]['candidates'][k]['det_bbox'])
                if len(pose_box) > 0: 
                    pose_box[2:] = pose_box[2:] + pose_box[:2]
                tracking_data_c[filmname][i][j]['candidates'][k]['det_bbox'] = pose_box

100%|██████████| 67/67 [00:00<00:00, 2094.03it/s]

100%|██████████| 44/44 [00:00<00:00, 3163.45it/s]

100%|██████████| 45/45 [00:00<00:00, 3058.76it/s]

100%|██████████| 23/23 [00:00<00:00, 1475.58it/s]

100%|██████████| 75/75 [00:00<00:00, 5250.14it/s]

100%|██████████| 20/20 [00:00<00:00, 972.63it/s]

100%|██████████| 10/10 [00:00<00:00, 3106.89it/s]

100%|██████████| 59/59 [00:00<00:00, 3166.65it/s]

100%|██████████| 47/47 [00:00<00:00, 2500.22it/s]

100%|██████████| 45/45 [00:00<00:00, 6719.49it/s]

100%|██████████| 16/16 [00:00<00:00, 4949.76it/s]

100%|██████████| 14/14 [00:00<00:00, 61.48it/s]


In [12]:
pose_rec_res_d = {filmname:[] for filmname in filmnames}

for filmname in filmnames:
    for scene_index in tqdm(range(len(tracking_data_c[filmname]))):
        
        pose_rec_res_d[filmname].append([])
        
        for frame_index in range(len(tracking_data_c[filmname][scene_index])):
            names, bboxes, keypoints, heatmaps = [], [], [], []
            for entity in tracking_data_c[filmname][scene_index][frame_index]['candidates']:            
                if entity['det_score'] > 0.5:
                    names.append(entity['track_id'])
                    bboxes.append(entity['det_bbox'].tolist())
                    keypoints.append(entity['pose_keypoints_2d'])
                    heatmaps.append(entity['heatmap'])
                    
            pose_rec_res_d[filmname][scene_index].append([names, bboxes, keypoints, heatmaps])

100%|██████████| 38/38 [00:00<00:00, 6468.49it/s]


In [173]:
def flat(data):
    return [item for sublist in data for item in sublist]

pose_data_t, face_data_t = {filmname:[] for filmname in filmnames}, {filmname:[] for filmname in filmnames} 

for filmname in filmnames:
    pose_f_data, face_f_data = [], []
    for s_idx in tqdm(range(len(pose_rec_res_d[filmname]))):
        pose_s_ids = set(flat([pose_rec_res_d[filmname][s_idx][i][0] for i in range(len(pose_rec_res_d[filmname][s_idx]))]))
        face_s_names = set(flat([face_rec_res_d[filmname][s_idx][i][0] for i in range(len(face_rec_res_d[filmname][s_idx]))]))
        
        pose_s_data, face_s_data = {pose_id:[] for pose_id in pose_s_ids}, {face_name:[] for face_name in face_s_names}
        print('Scene #', s_idx)
        for f_idx in range(len(pose_rec_res_d[filmname][s_idx])):

            frame_face_data = face_rec_res_d[filmname][s_idx][f_idx]
            
            local_face_names = [frame_face_data[0][i] for i in range(len(frame_face_data[0]))]
            
            flag = 0
            used_names = []
            
            print('---', f_idx, '/', len(face_rec_res_d[filmname][s_idx]))
            print(local_face_names)
            for i in range(len(frame_face_data[0])):
                current_name = frame_face_data[0][i]
                current_bbox = frame_face_data[1][i]
                for face_name in face_s_names:
                    if current_name == face_name and current_name not in used_names:
                        face_s_data[face_name].append(current_bbox[:4])
                        used_names.append(face_name)
                    else:
                        if face_name not in local_face_names and flag == 0:
                            face_s_data[face_name].append([])
                flag += 1
                
            if len(frame_face_data[0]) == 0:
                for face_name in face_s_names:
                    face_s_data[face_name].append([])
            
            for face_name in face_s_names:
                print(face_name, len(face_s_data[face_name]))            
            
            
            
            frame_pose_data = pose_rec_res_d[filmname][s_idx][f_idx]

            local_pose_ids = [frame_pose_data[0][i] for i in range(len(frame_pose_data[0]))]
#            print('---', f_idx, '/', len(pose_rec_res_d[filmname][s_idx]))
             
            flag = 0
                
            for i in range(len(frame_pose_data[0])):
                current_id = frame_pose_data[0][i]
                current_bbox = frame_pose_data[1][i]
                current_pose = frame_pose_data[2][i]
                current_heatmap = frame_pose_data[3][i]
#                print('current id', current_id)
#                print('local pose ids', local_pose_ids)
                
                
                
                for pose_id in pose_s_ids:
                    if current_id == pose_id:
                        pose_s_data[pose_id].append([current_bbox, current_pose, current_heatmap])
                    else:
                        if pose_id not in local_pose_ids and flag == 0:
                            pose_s_data[pose_id].append([[], [], []])
                flag += 1
                            
            if len(frame_pose_data[0]) == 0:
                for pose_id in pose_s_ids:
                    pose_s_data[pose_id].append([[], [], []])
                    
#            for pose_id in pose_s_ids:
#                print(pose_id, len(pose_s_data[pose_id]))
            
        pose_f_data.append(pose_s_data)
        face_f_data.append(face_s_data)
    pose_data_t[filmname] = pose_f_data
    face_data_t[filmname] = face_f_data

  6%|▌         | 4/67 [00:00<00:01, 34.09it/s]

Scene # 0
--- 0 / 63
[]
jack 1
--- 1 / 63
[]
jack 2
--- 2 / 63
[]
jack 3
--- 3 / 63
[]
jack 4
--- 4 / 63
[]
jack 5
--- 5 / 63
[]
jack 6
--- 6 / 63
[]
jack 7
--- 7 / 63
[]
jack 8
--- 8 / 63
['jack']
jack 9
--- 9 / 63
['jack']
jack 10
--- 10 / 63
['jack']
jack 11
--- 11 / 63
['jack']
jack 12
--- 12 / 63
['jack']
jack 13
--- 13 / 63
['jack']
jack 14
--- 14 / 63
['jack']
jack 15
--- 15 / 63
[]
jack 16
--- 16 / 63
['jack']
jack 17
--- 17 / 63
['jack']
jack 18
--- 18 / 63
['jack']
jack 19
--- 19 / 63
['jack']
jack 20
--- 20 / 63
['jack']
jack 21
--- 21 / 63
['jack']
jack 22
--- 22 / 63
['jack']
jack 23
--- 23 / 63
['jack']
jack 24
--- 24 / 63
['jack']
jack 25
--- 25 / 63
['jack']
jack 26
--- 26 / 63
['jack']
jack 27
--- 27 / 63
['jack']
jack 28
--- 28 / 63
['jack']
jack 29
--- 29 / 63
['jack']
jack 30
--- 30 / 63
['jack']
jack 31
--- 31 / 63
['jack']
jack 32
--- 32 / 63
['jack']
jack 33
--- 33 / 63
['jack']
jack 34
--- 34 / 63
['jack']
jack 35
--- 35 / 63
['jack']
jack 36
--- 36 / 63
['jack'

mr_sprague 47
--- 47 / 102
['gus_boulis']
 48
bill 48
gus_boulis 48
ralph 48
senator_bob 48
grover 48
mike 48
jack 48
pam 48
tom_delay 48
mr_sprague 48
--- 48 / 102
['', 'jack', '']
 49
bill 49
gus_boulis 49
ralph 49
senator_bob 49
grover 49
mike 49
jack 49
pam 49
tom_delay 49
mr_sprague 49
--- 49 / 102
[]
 50
bill 50
gus_boulis 50
ralph 50
senator_bob 50
grover 50
mike 50
jack 50
pam 50
tom_delay 50
mr_sprague 50
--- 50 / 102
[]
 51
bill 51
gus_boulis 51
ralph 51
senator_bob 51
grover 51
mike 51
jack 51
pam 51
tom_delay 51
mr_sprague 51
--- 51 / 102
[]
 52
bill 52
gus_boulis 52
ralph 52
senator_bob 52
grover 52
mike 52
jack 52
pam 52
tom_delay 52
mr_sprague 52
--- 52 / 102
['jack']
 53
bill 53
gus_boulis 53
ralph 53
senator_bob 53
grover 53
mike 53
jack 53
pam 53
tom_delay 53
mr_sprague 53
--- 53 / 102
['bill']
 54
bill 54
gus_boulis 54
ralph 54
senator_bob 54
grover 54
mike 54
jack 54
pam 54
tom_delay 54
mr_sprague 54
--- 54 / 102
['bill', 'mike']
 55
bill 55
gus_boulis 55
ralph 55
s

 16%|█▋        | 11/67 [00:00<00:03, 17.86it/s]

senator_bob 35
chief_poncho 35
mike 35
jack 35
art 35
--- 35 / 38
['gus_boulis', 'art']
 36
gus_boulis 36
senator_bob 36
chief_poncho 36
mike 36
jack 36
art 36
--- 36 / 38
[]
 37
gus_boulis 37
senator_bob 37
chief_poncho 37
mike 37
jack 37
art 37
--- 37 / 38
['mike']
 38
gus_boulis 38
senator_bob 38
chief_poncho 38
mike 38
jack 38
art 38
Scene # 8
--- 0 / 47
[]
 1
adam 1
bill 1
gus_boulis 1
scott 1
ralph 1
senator_bob 1
reverend_mueller 1
mike 1
jack 1
pam 1
emily 1
tom_delay 1
chris 1
mr_sprague 1
--- 1 / 47
['mike']
 2
adam 2
bill 2
gus_boulis 2
scott 2
ralph 2
senator_bob 2
reverend_mueller 2
mike 2
jack 2
pam 2
emily 2
tom_delay 2
chris 2
mr_sprague 2
--- 2 / 47
['bill']
 3
adam 3
bill 3
gus_boulis 3
scott 3
ralph 3
senator_bob 3
reverend_mueller 3
mike 3
jack 3
pam 3
emily 3
tom_delay 3
chris 3
mr_sprague 3
--- 3 / 47
['bill', 'ralph', 'bill', 'mike', '', 'gus_boulis', 'jack', 'gus_boulis']
 4
adam 4
bill 4
gus_boulis 4
scott 4
ralph 4
senator_bob 4
reverend_mueller 4
mike 4
jack 

...

 95%|█████████▍| 36/38 [00:01<00:00, 17.08it/s]

--- 12 / 37
['john']
helena 13
john 13
--- 13 / 37
['john']
helena 14
john 14
--- 14 / 37
['john']
helena 15
john 15
--- 15 / 37
['john']
helena 16
john 16
--- 16 / 37
['john']
helena 17
john 17
--- 17 / 37
['john']
helena 18
john 18
--- 18 / 37
[]
helena 19
john 19
--- 19 / 37
['john']
helena 20
john 20
--- 20 / 37
['john']
helena 21
john 21
--- 21 / 37
['john']
helena 22
john 22
--- 22 / 37
[]
helena 23
john 23
--- 23 / 37
[]
helena 24
john 24
--- 24 / 37
['helena']
helena 25
john 25
--- 25 / 37
['john']
helena 26
john 26
--- 26 / 37
['john']
helena 27
john 27
--- 27 / 37
['john']
helena 28
john 28
--- 28 / 37
['john']
helena 29
john 29
--- 29 / 37
['john']
helena 30
john 30
--- 30 / 37
['john', 'helena']
helena 31
john 31
--- 31 / 37
['helena', 'john']
helena 32
john 32
--- 32 / 37
['helena', 'john']
helena 33
john 33
--- 33 / 37
[]
helena 34
john 34
--- 34 / 37
[]
helena 35
john 35
--- 35 / 37
[]
helena 36
john 36
--- 36 / 37
[]
helena 37
john 37
Scene # 34
--- 0 / 51
[]
 1
jeremia

pastor 45
--- 45 / 65
['pastor']
 46
jeremias 46
joe 46
pastor 46
--- 46 / 65
[]
 47
jeremias 47
joe 47
pastor 47
--- 47 / 65
['']
 48
jeremias 48
joe 48
pastor 48
--- 48 / 65
['']
 49
jeremias 49
joe 49
pastor 49
--- 49 / 65
['']
 50
jeremias 50
joe 50
pastor 50
--- 50 / 65
[]
 51
jeremias 51
joe 51
pastor 51
--- 51 / 65
[]
 52
jeremias 52
joe 52
pastor 52
--- 52 / 65
[]
 53
jeremias 53
joe 53
pastor 53
--- 53 / 65
[]
 54
jeremias 54
joe 54
pastor 54
--- 54 / 65
[]
 55
jeremias 55
joe 55
pastor 55
--- 55 / 65
[]
 56
jeremias 56
joe 56
pastor 56
--- 56 / 65
[]
 57
jeremias 57
joe 57
pastor 57
--- 57 / 65
[]
 58
jeremias 58
joe 58
pastor 58
--- 58 / 65
[]
 59
jeremias 59
joe 59
pastor 59
--- 59 / 65
[]
 60
jeremias 60
joe 60
pastor 60
--- 60 / 65
[]
 61
jeremias 61
joe 61
pastor 61
--- 61 / 65
[]
 62
jeremias 62
joe 62
pastor 62
--- 62 / 65
[]
 63
jeremias 63
joe 63
pastor 63
--- 63 / 65
[]
 64
jeremias 64
joe 64
pastor 64
--- 64 / 65
[]
 65
jeremias 65
joe 65
pastor 65
Scene # 37
--- 0

100%|██████████| 38/38 [00:01<00:00, 23.25it/s]


['helena', 'pastor']
pastor 9
helena 9
john 9
--- 9 / 10
['helena', 'john']
pastor 10
helena 10
john 10


In [142]:
face_data_t['Bagman'][1]['susan']
len(pose_data_t['Bagman'][1][1])
len(pose_rec_res_d['Bagman'][2]), len(face_rec_res_d['Bagman'][2])

[[],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [264.93534088134766,
  196.28776130080223,
  481.32816302776337,
  487.91613173671067],
 [],
 [257.3000215291977,
  178.78430284559727,
  457.8292209729552,
  442.99148747324944],
 [255.74803319573402,
  173.54729824885726,
  440.76893220096827,
  411.30643117427826]]

In [ ]:
from sklearn.metrics.pairwise import euclidean_distances

def get_centroid_distance(face_box, pose_box):
    face_box_centroid = (face_box[0] + face_box[2])/2, (face_box[1] + face_box[3])/2
    pose_box_centroid = (2*pose_box[0] + pose_box[2])/2, (2*pose_box[1] + pose_box[3])/2

    return euclidean_distances([face_box_centroid, pose_box_centroid])[0][1]

def compute_distance(pose_entity, face_entity):

    nonzero_face, nonzero_pose =\
        [True if len(frame)>0 else False for frame in face_entity],\
        [True if len(frame[0])>0 else False  for frame in pose_entity]

    intersection_mask = np.logical_and(nonzero_face, nonzero_pose)

   
    face_bboxes = np.array(face_entity)[intersection_mask]
    pose_bboxes = [item[0] for item in np.array(pose_entity)[intersection_mask]]
#    print('---------')
#    print(face_bboxes)
#    print('   ')
#    print(pose_bboxes)
    
    if len(face_bboxes) > 0: 
        dist = np.mean([get_centroid_distance(face_box, pose_box) for face_box, pose_box in zip(face_bboxes,pose_bboxes)]) 
    else:
        dist = 100500

    return dist

face_2_pose_global = {filmname:[] for filmname in filmnames}

for filmname in filmnames:
    face_2_pose_f = []
    for s_idx in tqdm(range(len(pose_data_t[filmname]))):    
        face_trajs = face_data_t[filmname][s_idx]
        pose_trajs = pose_data_t[filmname][s_idx]
        
        ## actual matching of poses and faces in a scene
        
        face_2_pose = {entity:[] for entity in face_trajs}

        for i, pose_entity in enumerate(pose_trajs):
            candidate, min_dist = -1, 100500
            for face_entity in face_trajs:
#                print(filmname, s_idx, face_entity, pose_entity)
                dist = compute_distance(pose_trajs[pose_entity], face_trajs[face_entity])

                if dist < min_dist:
                    min_dist = dist
                    candidate = face_entity

            if candidate != -1:
                face_2_pose[candidate].append(i)

#        print(face_2_pose)
        
        def get_centroid_distance_wc(face_box, pose_box):
            face_box_centroid = (face_box[0] + face_box[2])/2, (face_box[1] + face_box[3])/2
            pose_box_centroid = (pose_box[0] + pose_box[2])/2, (pose_box[1] + pose_box[3])/2

            return euclidean_distances([face_box_centroid, pose_box_centroid])[0][1]

        def get_closest_bbox(face_bbox, pose_bboxes):
            index, min_dist = -1, 100500
            for i, pose_bbox in enumerate(pose_bboxes):

                dist = get_centroid_distance_wc(face_bbox, pose_bbox)
        #        print(f'From {face_bbox} to {pose_bbox} ({i}): \n {dist}')

                if dist < min_dist:
                    min_dist = dist
                    index = i
            return index
        
        scene_frames = videos[filmname][s_idx] 
        for i, frame in enumerate([i for i in range(len(scene_frames))]):
#            image_path = f'lighttrack/data/demo//{filmname}_{scene_number}_dr_{dec_rate}/frame{"".join(["0" for i in range(5-len(str(frame)))])}{frame}.jpg'
#            e = read_image(image_path)

            for face_entity in face_trajs:

                pose_entities_face = face_2_pose[face_entity] 
                pose_bbox = torch.tensor([0,0,0,0])
                pose_bboxes, pose_heatmaps = [], []

#                print('\n', face_trajs[face_entity][i])
#                print(pose_entities_face)
                if len(face_trajs[face_entity][i]) > 0:
                    face_bbox = torch.tensor(face_trajs[face_entity][i], dtype=torch.float)
        #            print('Related pose entities:', pose_entities_face)
                else:
                    face_bbox = torch.tensor([0,0,0,0])


                for pose_entity_face in pose_entities_face:
                    if len(pose_trajs[pose_entity_face][i][0]) > 0:
                        pose_bbox = torch.tensor(pose_trajs[pose_entity_face][i][0])
       #                 pose_bbox[[2,3]] = pose_bbox[[2,3]] + pose_bbox[[0,1]]

        #                print(str(face_entity), pose_bbox)
                        pose_heatmaps.append(pose_trajs[pose_entity_face][i][2])
                        pose_bboxes.append(pose_bbox)

                index = get_closest_bbox(face_bbox, pose_bboxes)
        #        print(f'Closest entity index: {index}')
                if index != -1:
                    face_trajs[face_entity][i] = {'face_bbox':face_trajs[face_entity][i], 'pose_box':pose_bboxes[index], 'pose_heatmap':pose_heatmaps[index]}
                    bboxes = torch.vstack([face_bbox, pose_bboxes[index]])
                else:
                    face_trajs[face_entity][i] = {'face_bbox':face_trajs[face_entity][i], 'pose_box':[], 'pose_heatmap':[]}
                    bboxes = torch.vstack([face_bbox, torch.tensor([0,0,0,0])])
#                e = draw_bounding_boxes(e, bboxes, width=5,
#                                             colors=[bbox_color_entity_dict[face_entity] for bbox in bboxes],
#                                             labels=[str(face_entity) for bbox in bboxes], font_size=538)


## Format standartization

In [204]:
 with open(f'evg_tracking_final.pickle', 'wb') as handle:
        pickle.dump(face_data_t, handle, protocol=pickle.HIGHEST_PROTOCOL)   

In [201]:
graphen_tracking = {filmname:[] for filmname in filmnames} 

for filmname in filmnames:
    film_data = []
    for s_index in range(len(videos[filmname])):
        
        names = ['' if len(entity['names']) == 0 else entity['names'] for entity in graphen_raw[filmname][s_index]]
        
        scene_data = {name:[] for name in names}
        
        for entity in graphen_raw[filmname][s_index]:    
            boxes = entity['boxes']
            frames = entity['frameID']
            if len(entity['names']) == 0:
                name = ''
            else:
                name = entity['names']
            
            print(name, names)
            
            sample = {'face_box':[], 'pose_box':[], 'pose_heatmap':[]}
            for f_index in range(len(videos[filmname][s_index])):
                if f_index in frames:
                    local_index = frames.index(f_index)
                    scene_data[name].append({'face_box':[], 'pose_box':boxes[local_index], 'pose_heatmap':[]})
                else:
                    scene_data[name].append({'face_box':[], 'pose_box':[], 'pose_heatmap':[]})
        film_data.append(scene_data)
    graphen_tracking[filmname] = film_data

jack ['jack', '']
 ['jack', '']
 ['', 'susan', '', '', '', 'gus_boulis', 'mr_sprague', '']
susan ['', 'susan', '', '', '', 'gus_boulis', 'mr_sprague', '']
 ['', 'susan', '', '', '', 'gus_boulis', 'mr_sprague', '']
 ['', 'susan', '', '', '', 'gus_boulis', 'mr_sprague', '']
 ['', 'susan', '', '', '', 'gus_boulis', 'mr_sprague', '']
gus_boulis ['', 'susan', '', '', '', 'gus_boulis', 'mr_sprague', '']
mr_sprague ['', 'susan', '', '', '', 'gus_boulis', 'mr_sprague', '']
 ['', 'susan', '', '', '', 'gus_boulis', 'mr_sprague', '']
jack ['jack', 'jack', 'pam', 'jack', '', '', 'mike', 'gus_boulis', '']
jack ['jack', 'jack', 'pam', 'jack', '', '', 'mike', 'gus_boulis', '']
pam ['jack', 'jack', 'pam', 'jack', '', '', 'mike', 'gus_boulis', '']
jack ['jack', 'jack', 'pam', 'jack', '', '', 'mike', 'gus_boulis', '']
 ['jack', 'jack', 'pam', 'jack', '', '', 'mike', 'gus_boulis', '']
 ['jack', 'jack', 'pam', 'jack', '', '', 'mike', 'gus_boulis', '']
mike ['jack', 'jack', 'pam', 'jack', '', '', 'mike', '

 ['', '', '', 'debbie', 'debbie', '', '', '', '', '', '', '']
 ['', '', '', 'debbie', 'debbie', '', '', '', '', '', '', '']
 ['', '', '', 'debbie', 'debbie', '', '', '', '', '', '', '']
 ['', '', '', 'debbie', 'debbie', '', '', '', '', '', '', '']
 ['', '', '', 'debbie', 'debbie', '', '', '', '', '', '', '']
 ['', '', '', 'debbie', 'debbie', '', '', '', '', '', '', '']
master ['master', 'officer2', 'wife2', 'wife2', 'master', '']
officer2 ['master', 'officer2', 'wife2', 'wife2', 'master', '']
wife2 ['master', 'officer2', 'wife2', 'wife2', 'master', '']
wife2 ['master', 'officer2', 'wife2', 'wife2', 'master', '']
master ['master', 'officer2', 'wife2', 'wife2', 'master', '']
 ['master', 'officer2', 'wife2', 'wife2', 'master', '']
 ['', '', 'mike', '', '', '']
 ['', '', 'mike', '', '', '']
mike ['', '', 'mike', '', '', '']
 ['', '', 'mike', '', '', '']
 ['', '', 'mike', '', '', '']
 ['', '', 'mike', '', '', '']
 ['', 'mike', '', 'mike', 'wife1', 'master', 'wife2', '', '', '']
mike ['', 'm

eisenheim ['inspector_uhi', 'prince_leopold', 'prince_leopold', 'prince_leopold', 'sophie', 'willigut', '', 'eisenheim', 'prince_leopold', 'prince_leopold', 'prince_leopold', 'willigut', '', 'prince_leopold', 'willigut', 'willigut', 'inspector_uhi', 'prince_leopold', 'doctor', 'eisenheim', '', 'prince_leopold', 'eisenheim', 'prince_leopold', 'eisenheim', 'eisenheim', 'travelling_magician', 'prince_leopold', 'prince_leopold', '']
eisenheim ['inspector_uhi', 'prince_leopold', 'prince_leopold', 'prince_leopold', 'sophie', 'willigut', '', 'eisenheim', 'prince_leopold', 'prince_leopold', 'prince_leopold', 'willigut', '', 'prince_leopold', 'willigut', 'willigut', 'inspector_uhi', 'prince_leopold', 'doctor', 'eisenheim', '', 'prince_leopold', 'eisenheim', 'prince_leopold', 'eisenheim', 'eisenheim', 'travelling_magician', 'prince_leopold', 'prince_leopold', '']
travelling_magician ['inspector_uhi', 'prince_leopold', 'prince_leopold', 'prince_leopold', 'sophie', 'willigut', '', 'eisenheim', 'pr

matt ['matt', '', 'matt', 'kaylee', 'matt', '', '', '', '', '', '', 'leon', 'leon', 'leon', 'leon', 'matt', '', '', '', '', 'kaylee']
 ['matt', '', 'matt', 'kaylee', 'matt', '', '', '', '', '', '', 'leon', 'leon', 'leon', 'leon', 'matt', '', '', '', '', 'kaylee']
 ['matt', '', 'matt', 'kaylee', 'matt', '', '', '', '', '', '', 'leon', 'leon', 'leon', 'leon', 'matt', '', '', '', '', 'kaylee']
 ['matt', '', 'matt', 'kaylee', 'matt', '', '', '', '', '', '', 'leon', 'leon', 'leon', 'leon', 'matt', '', '', '', '', 'kaylee']
 ['matt', '', 'matt', 'kaylee', 'matt', '', '', '', '', '', '', 'leon', 'leon', 'leon', 'leon', 'matt', '', '', '', '', 'kaylee']
 ['matt', '', 'matt', 'kaylee', 'matt', '', '', '', '', '', '', 'leon', 'leon', 'leon', 'leon', 'matt', '', '', '', '', 'kaylee']
 ['matt', '', 'matt', 'kaylee', 'matt', '', '', '', '', '', '', 'leon', 'leon', 'leon', 'leon', 'matt', '', '', '', '', 'kaylee']
leon ['matt', '', 'matt', 'kaylee', 'matt', '', '', '', '', '', '', 'leon', 'leon', 'l

robin ['robin', 'robin', '', 'john', 'john', 'alexander', 'sniper', 'john', 'robin', 'sniper', 'alexander']
robin ['robin', 'robin', '', 'john', 'john', 'alexander', 'sniper', 'john', 'robin', 'sniper', 'alexander']
 ['robin', 'robin', '', 'john', 'john', 'alexander', 'sniper', 'john', 'robin', 'sniper', 'alexander']
john ['robin', 'robin', '', 'john', 'john', 'alexander', 'sniper', 'john', 'robin', 'sniper', 'alexander']
john ['robin', 'robin', '', 'john', 'john', 'alexander', 'sniper', 'john', 'robin', 'sniper', 'alexander']
alexander ['robin', 'robin', '', 'john', 'john', 'alexander', 'sniper', 'john', 'robin', 'sniper', 'alexander']
sniper ['robin', 'robin', '', 'john', 'john', 'alexander', 'sniper', 'john', 'robin', 'sniper', 'alexander']
john ['robin', 'robin', '', 'john', 'john', 'alexander', 'sniper', 'john', 'robin', 'sniper', 'alexander']
robin ['robin', 'robin', '', 'john', 'john', 'alexander', 'sniper', 'john', 'robin', 'sniper', 'alexander']
sniper ['robin', 'robin', '', '

In [203]:
 with open(f'graphen_tracking_final.pickle', 'wb') as handle:
        pickle.dump(graphen_tracking, handle, protocol=pickle.HIGHEST_PROTOCOL)   

In [202]:
graphen_tracking['Bagman'][0]

{'jack': [{'face_box': [], 'pose_box': [], 'pose_heatmap': []},
  {'face_box': [], 'pose_box': [], 'pose_heatmap': []},
  {'face_box': [], 'pose_box': [], 'pose_heatmap': []},
  {'face_box': [], 'pose_box': [], 'pose_heatmap': []},
  {'face_box': [], 'pose_box': [], 'pose_heatmap': []},
  {'face_box': [], 'pose_box': [], 'pose_heatmap': []},
  {'face_box': [], 'pose_box': [], 'pose_heatmap': []},
  {'face_box': [], 'pose_box': [], 'pose_heatmap': []},
  {'face_box': [],
   'pose_box': tensor([ 700.7363,   82.6048, 1278.7936,  661.8593]),
   'pose_heatmap': []},
  {'face_box': [],
   'pose_box': tensor([ 681.2835,   90.9574, 1274.4246,  655.1149]),
   'pose_heatmap': []},
  {'face_box': [],
   'pose_box': tensor([ 680.5066,   88.4136, 1280.0000,  663.3273]),
   'pose_heatmap': []},
  {'face_box': [],
   'pose_box': tensor([ 676.0629,   78.3313, 1277.1588,  658.2806]),
   'pose_heatmap': []},
  {'face_box': [],
   'pose_box': tensor([ 680.3070,   75.5375, 1280.0000,  672.6663]),
   'pose

In [197]:
len(videos['Bagman'])

67

In [195]:
len(graphen_raw['Bagman'])

67

In [199]:
%debug

> /tmp/ipykernel_18878/3985270594.py(25)<module>()
     23                     scene_data[name].append({'face_box':[], 'pose_box':boxes[local_index], 'pose_heatmap':[]})
     24                 else:
---> 25                     scene_data[name].append({'face_box':[], 'pose_box':[], 'pose_heatmap':[]})
     26         film_data.append(scene_data)
     27     graphen_tracking[filmname] = film_data

ipdb> scene_data
{'debbie': [], '': [], 'mike': []}
ipdb> exit


In [178]:
graphen_raw['Bagman'][0][0]

{'centers': [tensor([989.7650, 372.2320]),
  tensor([977.8540, 373.0361]),
  tensor([980.2533, 375.8704]),
  tensor([976.6108, 368.3060]),
  tensor([980.1535, 374.1019]),
  tensor([913.6725, 365.7721]),
  tensor([963.8875, 367.2545]),
  tensor([899.7656, 361.8685]),
  tensor([989.9820, 392.2605]),
  tensor([1037.9159,  387.7029]),
  tensor([1052.0250,  379.8728]),
  tensor([1051.7224,  412.0578]),
  tensor([1052.3894,  387.3372]),
  tensor([1047.8333,  393.6502]),
  tensor([1029.8297,  404.4381]),
  tensor([1020.6432,  402.3293]),
  tensor([1021.8666,  405.7228]),
  tensor([1020.1294,  402.9242]),
  tensor([1006.7531,  406.9757]),
  tensor([988.7281, 390.3420]),
  tensor([984.2996, 397.8439]),
  tensor([1000.4614,  381.7254]),
  tensor([991.3308, 392.9061]),
  tensor([987.0448, 400.8248]),
  tensor([1011.1664,  402.4603]),
  tensor([998.2217, 400.8077]),
  tensor([1002.0012,  386.4617]),
  tensor([990.3480, 388.8428]),
  tensor([973.5610, 390.8127]),
  tensor([992.4965, 392.1533]),
  t

In [175]:
face_data_t['Bagman'][4]['jack']

[{'face_bbox': [], 'pose_box': [], 'pose_heatmap': []},
 {'face_bbox': [], 'pose_box': [], 'pose_heatmap': []},
 {'face_bbox': [], 'pose_box': [], 'pose_heatmap': []},
 {'face_bbox': [], 'pose_box': [], 'pose_heatmap': []},
 {'face_bbox': [], 'pose_box': [], 'pose_heatmap': []},
 {'face_bbox': [], 'pose_box': [], 'pose_heatmap': []},
 {'face_bbox': [], 'pose_box': [], 'pose_heatmap': []},
 {'face_bbox': [], 'pose_box': [], 'pose_heatmap': []},
 {'face_bbox': [], 'pose_box': [], 'pose_heatmap': []},
 {'face_bbox': [], 'pose_box': [], 'pose_heatmap': []},
 {'face_bbox': [], 'pose_box': [], 'pose_heatmap': []},
 {'face_bbox': [], 'pose_box': [], 'pose_heatmap': []},
 {'face_bbox': [], 'pose_box': [], 'pose_heatmap': []},
 {'face_bbox': [], 'pose_box': [], 'pose_heatmap': []},
 {'face_bbox': [489.8134809732437,
   82.92980280518532,
   659.7348870933056,
   353.6096388399601],
  'pose_box': tensor([ 373.6254,   47.2990, 1034.6254,  723.2991]),
  'pose_heatmap': [0.023915134303288867,
   0.

In [ ]:
with open(f'eg_tracking.pickle', 'wb') as handle:
    pickle.dump(entityList_f[filmname], handle, protocol=pickle.HIGHEST_PROTOCOL)

In [111]:
%debug

> /tmp/ipykernel_18878/1047109393.py(58)get_centroid_distance_wc()
     56         def get_centroid_distance_wc(face_box, pose_box):
     57             face_box_centroid = (face_box[0] + face_box[2])/2, (face_box[1] + face_box[3])/2
---> 58             pose_box_centroid = (pose_box[0] + pose_box[2])/2, (pose_box[1] + pose_box[3])/2
     59 
     60             return euclidean_distances([face_box_centroid, pose_box_centroid])[0][1]

ipdb> pose_box
tensor([])
ipdb> face_box
tensor([0, 0, 0, 0])
ipdb> учше
*** NameError: name 'учше' is not defined
ipdb> exit


In [58]:
len(pose_data_t['Bagman'][0][1])

12

In [35]:
len(face_data_t['Bagman'][0]['jack'])

54

In [36]:
pose_data_t['Bagman'][0].keys()

dict_keys([0, 1])